The weak formulation is


$a_D(u,v)+a_S(u,v)+a_I(u,v)+b(v,p)+b(u,q)=\int_{\Omega_S}f_Svdx+\int_{\Omega_D}f_Dqdx$
where
\begin{align}
a_{S}(u,v)&=\sum_{T\in \mathcal{T_S}}2\mu\int_T\epsilon(u):\epsilon(v)dx-\sum_{F\in\mathcal{F^i_S}}\int_{F}2\mu\{\{\epsilon(u)\}\}n\cdot[[v]]ds-\sum_{F\in\mathcal{F^i_S}}\int_{F}2\mu\{\{\epsilon(v)\}\}n\cdot[[u]]ds\\
&+\sum_{F\in \mathcal{F}^i_S}\frac{\sigma k^2}{h}\int_{F}[[u]][[v]]ds+\sum_{F\in\mathcal{F_S}}\frac{2\sigma k^2}{h}\int_{F}uvds
\end{align}

$a_D(u, v)=\sum_{T\in \mathcal{T_D}}2\mu\int_T \kappa^{-1}uvdx$ 

$a_I(u,v) =\sum_{F\in F_{SD,h}}\int_F\alpha \kappa^{-1/2}u^tv^t$

$b(v,q)=-\int_\Omega \nabla\cdot vqdx$.



In [8]:
from ngsolve import *
from netgen.geom2d import SplineGeometry
from math import pi
#  (0,1)        Gamma_S         (1,1)
#        +----------------------+  
#        |     Stokes           | 
#Gamma_S |                      | Gamma_S
#        |        Gamma_I       |
#(0,0.5) +----------------------+ (1,0.5)
#        |                      |          
#Gamma_D |                      | Gamma_D
#        |   Darcy              |
#        +----------------------+
#  (0,0)      Gamma_D           (1,0)
#
geo = SplineGeometry()
points     = [ (0, 0), (1, 0),  (1, 0.5), (1, 1), (0, 1), (0, 0.5)]
pnums    = [geo.AppendPoint(*pt) for pt in points]
lines = [ (pnums[0], pnums[1], "gammaD",  2, 0),
          (pnums[1], pnums[2], "gammaD",  2, 0), 
          (pnums[2], pnums[3], "gammaS",  1, 0),
          (pnums[3], pnums[4], "gammaS",  1, 0),
          (pnums[4], pnums[5], "gammaS",  1, 0),
          (pnums[5], pnums[0], "gammaD",  2, 0),
          (pnums[5], pnums[2], "gammaI",  1, 2)]
for p1,p2,bc,ml,mr in lines:
    geo.Append( ["line", p1, p2], bc=bc, leftdomain=ml, rightdomain=mr)
geo.SetMaterial(1, "stokes")
geo.SetMaterial(2, "darcy")
mesh = Mesh( geo.GenerateMesh(maxh=0.2) )

Draw(mesh)

#Inteface Indicator
def GetInterfaceIndicator(mesh):
    dom_indicator = GridFunction(L2(mesh,order=0))
    dom_indicator.Set(CoefficientFunction([1,2]))
  
    ffes = FacetFESpace(mesh,order=0)
    dom_ind_average = GridFunction(ffes)
    mf = BilinearForm(ffes,symmetric=True)
    mf += SymbolicBFI(ffes.TrialFunction()*ffes.TestFunction(),element_boundary=True)
    mf.Assemble()
    ff = LinearForm(ffes)
    ff += SymbolicLFI(dom_indicator*ffes.TestFunction(),element_boundary=True)
    ff.Assemble()
    dom_ind_average.vec.data = mf.mat.Inverse() * ff.vec

    interface_indicator = BitArray(ffes.ndof)
    for i in range(len(dom_ind_average.vec)):
        if (dom_ind_average.vec[i] > 1.75) or (dom_ind_average.vec[i] < 1.25):
            interface_indicator[i] = False
        else:
            interface_indicator[i] = True
    
    return interface_indicator

interface_indicator = GetInterfaceIndicator(mesh)

k = 2 #order
V = HDiv(mesh, order=k, dirichlet="gammaS|gammaD", RT=True)#Raviart Thomas
Q = L2(mesh,order=k)
R = NumberSpace(mesh) 
X = FESpace([V,Q,R], dgjumps=True)
(u,p, lam1), (v,q, lam2) = X.TnT()
n = specialcf.normal(mesh.dim)  
h = specialcf.mesh_size 
# Parameter
kappa=1
mu=1
alpha= 0.1 
sigma= (k+1)*(k+2)/h
#gradient
du = grad(u)
dv = grad(v)
du1= grad(u.Other())
dv1= grad(v.Other())
#epsilon tensor
eps_u = 0.5*(du+du.trans)
eps_u1 = 0.5*(du1+du1.trans)

eps_v = 0.5*(dv+dv.trans)
eps_v1 = 0.5*(dv1+dv1.trans)

#tangent
def tangent(vec):
    return vec - (vec*n)*n
#jumps
jump_u = u-u.Other()
jump_v = v-v.Other()

#average epsilon
average_epsu = 0.5*(eps_u+eps_u1)
average_epsv = 0.5*(eps_v+eps_v1)

a = BilinearForm(X)
# Stokes
#ah_S(U,V)
ahS_dx = 2*mu*InnerProduct(eps_u, eps_v) 
ahS_ds_interior = (sigma*k*k/h)*InnerProduct(jump_u, jump_v) \
              - 2*mu*InnerProduct ( average_epsu*n, jump_v ) \
              - 2*mu*InnerProduct ( average_epsv*n, jump_u)
ahS_ds =(2*sigma*k*k/h)*u*v

#bh(p,v)+bh(q,u)
bh_dx = - div(u)*q - div(v)*p 

# Darcy
#ah_D
ahD_dx = (1/kappa)*u*v 

# interface Gamma_I
ah_I = alpha*sqrt(1/kappa)*tangent(u)*tangent(v)
   
interface_term = ah_I

a += bh_dx*dx
a += ahD_dx*dx(definedon=mesh.Materials("darcy"))

a += ahS_dx*dx(definedon=mesh.Materials("stokes"))
a += ahS_ds*dx(element_boundary = True, definedon=mesh.Materials("stokes") )
a += ahS_ds_interior*dx(skeleton = True, definedon=mesh.Materials("stokes") )

a += (p*lam1 + q*lam2)*dx

interfacebfi = SymbolicBFI (interface_term, VOL, skeleton=True) 
interfacebfi.SetDefinedOnElements(interface_indicator)
a += interfacebfi

# Linear form
f  = LinearForm(X)

a.Assemble()
f.Assemble()

gfu = GridFunction(X)



#Solve
inv = a.mat.Inverse(freedofs=X.FreeDofs(), inverse="umfpack") 
res = f.vec.CreateVector() 
res.data = f.vec - a.mat*gfu.vec 
gfu.vec.data += inv * res


NgException: UmfpackInverse: Numeric factorization failed.